#  **<span style="color:orange"><center>Insurance Cost Predicion</span>**

# Setting up enviroment

In [0]:
!pip install pycaret

In [2]:
from pycaret.utils import enable_colab
enable_colab()

Colab mode activated.


In [3]:
from pycaret.regression import *

#Brief overview of techniques used for cleaning the dataset



Before we into the practical execution of the techniques mentioned above in Section 1, it is important to understand what are these techniques are and when to use them. More often than not most of these techniques will help linear and parametric algorithms, however it is not surprising to also see performance gains in tree-based models. The Below explanations are only brief and we recommend that you do extra reading to dive deeper and get a more thorough understanding of these techniques.

- **Normalization:** Normalization / Scaling (often used interchangeably with standardization) is used to transform the actual values of numeric variables in a way that provides helpful properties for machine learning. Many algorithms such as Linear Regression, Support Vector Machine and K Nearest Neighbors assume that all features are centered around zero and have variances that are at the same level of order. If a particular feature in a dataset has a variance that is larger in order of magnitude than other features, the model may not understand all features correctly and could perform poorly. __[Read more](https://sebastianraschka.com/Articles/2014_about_feature_scaling.html#z-score-standardization-or-min-max-scaling)__ <br/>
<br/>
- **Transformation:** While normalization transforms the range of data to remove the impact of magnitude in variance, transformation is a more radical technique as it changes the shape of the distribution so that transformed data can be represented by a normal or approximate normal distirbution. In general, you should transform the data if using algorithms that assume normality or a gaussian distribution. Examples of such models are Linear Regression, Lasso Regression and Ridge Regression. __[Read more](https://en.wikipedia.org/wiki/Power_transform)__<br/>
<br/>
- **Target Transformation:** This is similar to the `transformation` technique explained above with the exception that this is only applied to the target variable. __[Read more](https://scikit-learn.org/stable/auto_examples/compose/plot_transformed_target.html)__ to understand the effects of transforming the target variable in regression.<br/>
<br/>
- **Combine Rare Levels:** Sometimes categorical features have levels that are insignificant in the frequency distribution. As such, they may introduce noise into the dataset due to a limited sample size for learning. One way to deal with rare levels in categorical features is to combine them into a new class. <br/>
<br/>
- **Bin Numeric Variables:** Binning or discretization is the process of transforming numerical variables into categorical features. An example would be `Carat Weight` in this experiment. It is a continious distribution of numeric values that can be discretized into intervals. Binning may improve the accuracy of a predictive model by reducing the noise or non-linearity in the data. PyCaret automatically determines the number and size of bins using Sturges rule.  __[Read more](https://www.vosesoftware.com/riskwiki/Sturgesrule.php)__<br/>
<br/>
- **Model Ensembling and Stacking:** Ensemble modeling is a process where multiple diverse models are created to predict an outcome. This is achieved either by using many different modeling algorithms or using different samples of training data sets. The ensemble model then aggregates the predictions of each base model resulting in one final prediction for the unseen data. The motivation for using ensemble models is to reduce the generalization error of the prediction. As long as the base models are diverse and independent, the prediction error of the model decreases when the ensemble approach is used. The two most common methods in ensemble learning are `Bagging` and `Boosting`. Stacking is also a type of ensemble learning where predictions from multiple models are used as input features for a meta model that predicts the final outcome. __[Read more](https://blog.statsbot.co/ensemble-learning-d1dcd548e936)__<br/>
<br/>
- **Tuning Hyperparameters of Ensemblers:** Similar to hyperparameter tuning for a single machine learning model, we will also learn how to tune hyperparameters for an ensemble model.

#Getting the Data

In [4]:
from pycaret.datasets import get_data
dataset = get_data('insurance', profile=True)

/usr/local/lib/python3.6/dist-packages/statsmodels/tools/_testing.py:19: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


Notice that when the `profile` parameter is to `True`, it displays a data profile for exploratory data analysis. Several pre-processing steps as discussed above will be performed in this experiment based on this analysis. 

In [5]:
#check the shape of data
dataset.shape

(1338, 7)

In order to demonstrate the `predict_model()` function on unseen data, 10% of the data has been withheld from the original dataset to be used for predictions. This should not be confused with a train/test split as this particular split is performed to simulate a real life scenario. 

In [6]:
data = dataset.sample(frac=0.9, random_state=786).reset_index(drop=True)
data_unseen = dataset.drop(data.index).reset_index(drop=True)

print('Data for Modeling: ' + str(data.shape))
print('Unseen Data For Predictions ' + str(data_unseen.shape))

Data for Modeling: (1204, 7)
Unseen Data For Predictions (134, 7)


# Setting up Environment in PyCaret

In [0]:
from pycaret.regression import *

In [7]:
exp_reg102 = setup(data, target = 'charges', session_id = 123,
           normalize = True,
           polynomial_features = True, trigonometry_features = True, feature_interaction=True, 
           bin_numeric_features= ['age', 'bmi'])

 
Setup Succesfully Completed!


In [10]:
exp_reg102[0].columns

Index(['age_Power2', 'bmi_Power2', 'sex_male', 'children_0', 'children_1',
       'children_2', 'children_3', 'children_4', 'children_5', 'smoker_no',
       'region_northeast', 'region_northwest', 'region_southeast',
       'region_southwest', 'age_0.0', 'age_1.0', 'age_10.0', 'age_11.0',
       'age_2.0', 'age_3.0', 'age_4.0', 'age_5.0', 'age_6.0', 'age_7.0',
       'age_8.0', 'age_9.0', 'bmi_0.0', 'bmi_1.0', 'bmi_10.0', 'bmi_11.0',
       'bmi_2.0', 'bmi_3.0', 'bmi_4.0', 'bmi_5.0', 'bmi_6.0', 'bmi_7.0',
       'bmi_8.0', 'bmi_9.0', 'children_1_multiply_age_Power2',
       'bmi_7.0_multiply_age_Power2', 'smoker_no_multiply_children_0',
       'age_Power2_multiply_bmi_6.0', 'bmi_6.0_multiply_age_Power2',
       'sex_male_multiply_age_Power2', 'bmi_Power2_multiply_age_Power2',
       'sex_male_multiply_bmi_Power2', 'age_Power2_multiply_smoker_no',
       'smoker_no_multiply_bmi_Power2', 'children_1_multiply_bmi_Power2',
       'region_southeast_multiply_bmi_Power2', 'smoker_no_multiply

# Comparing All Models

In [8]:
compare_models()

#Ensemble a Model

### Blending

Blending is another common technique for ensembling that can be used in PyCaret. It creates multiple models and then averages the individual predictions to form a final prediction. If no list is passed, PyCaret uses all of the models available in the model library by default. Let's see an example below:

In [11]:
blend_all = blend_models()

MAE           MSE  ...   RMSLE          MAPE
0     2.933750e+03  2.025778e+07  ...  0.4299  3.635000e-01
1     1.150044e+14  1.124212e+30  ...  2.8528  2.584288e+09
2     2.701868e+03  1.624920e+07  ...  0.4087  3.523000e-01
3     3.076718e+03  2.639524e+07  ...  0.4939  3.445000e-01
4     3.005766e+03  2.953093e+07  ...  0.4237  2.477000e-01
5     3.520880e+03  2.804933e+07  ...  0.6172  4.065000e-01
6     1.438109e+04  3.397924e+08  ...  1.2840  1.785800e+00
7     2.701887e+03  2.236414e+07  ...  0.4649  3.634000e-01
8     2.392756e+03  1.286515e+07  ...  0.4087  3.761000e-01
9     3.002050e+03  2.857025e+07  ...  0.4816  3.235000e-01
Mean  1.150044e+13  1.124212e+29  ...  0.7865  2.584288e+08
SD    3.450133e+13  3.372636e+29  ...  0.7329  7.752865e+08

[12 rows x 6 columns]

Now that we have created a voting regressor using the `blend_models()` function. The model stored in the variable `blend_all` is just like any other model that you would create using `create_model()` or `tune_model()`. You can use this model for predictions on unseen data using `predict_model()` in the same way you would for any other model. Notice that since we didn't pass the list of specific models for voting, it uses all of the models in the model library by default. The next example will show how to pass a specific set of models for blending.

In [0]:
"""
we will create 3 specific models to be passed into blend_models().
Note that verbose is set to False to avoid printing score grid of individual models.
"""
xgboost = create_model('xgboost', verbose = False)
gbr = create_model('gbr', verbose = False)
catboost = create_model('catboost', verbose = False)
ridge=create_model('ridge',verbose=False)
huber = create_model('huber', verbose=False)

In [23]:
blend_specific_1 = blend_models(estimator_list = [xgboost,gbr,catboost])

MAE           MSE       RMSE      R2   RMSLE    MAPE
0     2476.9678  1.831498e+07  4279.6005  0.8833  0.4273  0.3163
1     1627.0145  6.441511e+06  2538.0132  0.9659  0.2991  0.2487
2     2432.5497  1.722952e+07  4150.8457  0.8666  0.4269  0.3498
3     2851.1386  2.691603e+07  5188.0663  0.7680  0.5166  0.2770
4     2964.2989  3.145581e+07  5608.5475  0.8009  0.4521  0.2403
5     2564.2409  1.970392e+07  4438.9093  0.8629  0.4265  0.3190
6     3012.1151  2.646715e+07  5144.6230  0.8545  0.4822  0.3915
7     2561.2114  2.330980e+07  4828.0224  0.7820  0.4500  0.2981
8     2106.7925  1.214327e+07  3484.7197  0.9400  0.3854  0.3219
9     2465.9684  2.777308e+07  5270.0166  0.7559  0.4563  0.2391
Mean  2506.2298  2.097551e+07  4493.1364  0.8480  0.4323  0.3002
SD     391.3532  7.341074e+06   887.2603  0.0676  0.0556  0.0473

In [24]:
blend_specific_2 = blend_models(estimator_list = [xgboost,gbr,catboost,ridge])

MAE           MSE       RMSE      R2   RMSLE    MAPE
0     2515.5991  1.786054e+07  4226.1738  0.8862  0.4128  0.3110
1     1828.1290  7.122695e+06  2668.8378  0.9623  0.3034  0.2578
2     2448.2934  1.619207e+07  4023.9369  0.8746  0.4132  0.3330
3     2744.4616  2.509287e+07  5009.2781  0.7837  0.4892  0.2709
4     2944.3157  3.006265e+07  5482.9416  0.8097  0.4420  0.2417
5     2596.3316  1.908657e+07  4368.8177  0.8672  0.4218  0.3263
6     2946.3715  2.344974e+07  4842.4932  0.8711  0.4550  0.3691
7     2535.0544  2.271771e+07  4766.3101  0.7876  0.4375  0.2904
8     1970.5727  1.090529e+07  3302.3165  0.9461  0.3693  0.3090
9     2488.1683  2.732571e+07  5227.3995  0.7598  0.4541  0.2461
Mean  2501.7297  1.998158e+07  4391.8505  0.8548  0.4198  0.2955
SD     346.6504  6.845393e+06   832.6064  0.0651  0.0492  0.0395

In [43]:
blend_specific_3 = blend_models(estimator_list = [xgboost,gbr,catboost,ridge, huber])

MAE           MSE       RMSE      R2   RMSLE    MAPE
0     2382.2645  1.754017e+07  4188.0992  0.8882  0.3897  0.2662
1     1796.7329  7.704956e+06  2775.7802  0.9592  0.2636  0.2162
2     2303.1086  1.531914e+07  3913.9675  0.8814  0.3821  0.2812
3     2586.7173  2.452471e+07  4952.2432  0.7886  0.4778  0.2343
4     2817.4201  2.932912e+07  5415.6367  0.8144  0.4327  0.2126
5     2492.9521  1.908626e+07  4368.7825  0.8672  0.3977  0.2789
6     2733.9466  2.167678e+07  4655.8334  0.8809  0.4231  0.3114
7     2392.5583  2.279425e+07  4774.3325  0.7868  0.4280  0.2491
8     1842.9706  1.032043e+07  3212.5432  0.9490  0.3295  0.2569
9     2417.5399  2.802176e+07  5293.5582  0.7537  0.4467  0.2157
Mean  2376.6211  1.963176e+07  4355.0777  0.8569  0.3971  0.2523
SD     317.5021  6.743707e+06   815.5109  0.0658  0.0588  0.0313

### Stacking

In [15]:
stack_1 = stack_models([xgboost,gbr,catboost])

MAE           MSE       RMSE      R2   RMSLE    MAPE
0     2710.4451  1.912323e+07  4373.0119  0.8782  0.4581  0.3232
1     2400.7478  1.218354e+07  3490.4933  0.9356  0.3381  0.3008
2     2770.0776  1.710169e+07  4135.4187  0.8676  0.4081  0.3346
3     2799.7085  2.375735e+07  4874.1507  0.7952  0.4904  0.2621
4     3206.8705  3.180140e+07  5639.2731  0.7987  0.4743  0.2632
5     2854.3041  2.179608e+07  4668.6269  0.8484  0.4509  0.3558
6     3173.2611  2.324292e+07  4821.0908  0.8723  0.4389  0.3607
7     2711.3178  2.366995e+07  4865.1775  0.7786  0.4551  0.3046
8     2106.4690  1.078192e+07  3283.5839  0.9468  0.3842  0.3298
9     2670.8192  2.782245e+07  5274.6989  0.7554  0.4788  0.2643
Mean  2740.4021  2.112805e+07  4542.5526  0.8477  0.4377  0.3099
SD     307.5959  6.199243e+06   702.3311  0.0616  0.0451  0.0354

In [19]:
stack_1 = stack_models([xgboost,gbr,catboost,ridge])

MAE           MSE       RMSE      R2   RMSLE    MAPE
0     2124.5172  9.968707e+06  3157.3259  0.9365  0.4868  0.2629
1     2566.1734  2.203646e+07  4694.3009  0.8834  0.4168  0.2882
2     2231.7965  1.045775e+07  3233.8451  0.9190  0.3372  0.2539
3     2684.1960  1.814309e+07  4259.4704  0.8436  0.4410  0.3046
4     3034.1984  2.030302e+07  4505.8873  0.8715  0.4325  0.3252
5     2200.5464  1.107283e+07  3327.5865  0.9230  0.3405  0.2637
6     2375.7411  1.386541e+07  3723.6283  0.9238  0.3379  0.2610
7     2666.0186  1.600054e+07  4000.0680  0.8504  0.5203  0.4460
8     2040.0343  7.516428e+06  2741.6105  0.9629  0.5929  0.3394
9     2897.3191  1.922951e+07  4385.1460  0.8310  0.4713  0.3898
Mean  2482.0541  1.485937e+07  3802.8869  0.8945  0.4377  0.3135
SD     321.7889  4.741989e+06   630.4174  0.0424  0.0803  0.0602

Before we wrap up this section, there is another parameter in `stack_models()` that we haven't seen yet called `restack`. This parameter controls the ability to expose the raw data to the meta model. When set to `True`, it exposes the raw data to the meta model along with all the predictions of the base level models. By default it is set to `True`. See the example below with the `restack` parameter changed to `False`.

In [28]:
stack_2 = stack_models([xgboost,gbr,catboost,ridge], restack = False)

MAE           MSE       RMSE      R2   RMSLE    MAPE
0     2541.2435  1.766332e+07  4202.7748  0.8875  0.4018  0.3081
1     2106.6237  9.168611e+06  3027.9715  0.9515  0.3105  0.2721
2     2504.8020  1.558575e+07  3947.8788  0.8793  0.3995  0.3225
3     2730.3236  2.423044e+07  4922.4423  0.7911  0.4810  0.2587
4     2948.5749  2.936675e+07  5419.1100  0.8141  0.4382  0.2374
5     2721.6126  2.073071e+07  4553.0991  0.8558  0.4331  0.3419
6     2882.1589  2.250515e+07  4743.9596  0.8763  0.4369  0.3445
7     2523.1255  2.259294e+07  4753.2027  0.7887  0.4423  0.2853
8     1982.0847  1.035097e+07  3217.2928  0.9489  0.3686  0.3164
9     2532.2683  2.709444e+07  5205.2318  0.7618  0.4552  0.2538
Mean  2547.2818  1.992891e+07  4399.2963  0.8555  0.4167  0.2941
SD     292.1218  6.362505e+06   758.3531  0.0625  0.0464  0.0360

#  Predict on test / hold-out Sample

In [45]:
predict_model(blend_specific_3);

Model       MAE           MSE       RMSE      R2   RMSLE    MAPE
0  Voting Regressor  2537.516  2.305581e+07  4801.6469  0.8253  0.4227  0.2548

#  Finalize Model for Deployment

In [31]:
save_model(blend_specific_3, 'deployment_14052020')

Transformation Pipeline and Model Succesfully Saved


In [46]:
final_blend_3 = finalize_model(blend_specific_3)

#  Predict on unseen data

We will now use `blend-specific_3` to generate predictions on `data_unseen` which is the variable created at the beginning of the tutorial and contains 10% of the original dataset which was never exposed to PyCaret. 

In [47]:
unseen_predictions = predict_model(blend_specific_3, data=data_unseen, round=0)
unseen_predictions.head()

age     sex     bmi  children smoker     region      charges    Label
0   18  female  27.280         3    yes  southeast  18223.45120  20409.0
1   35    male  17.860         1     no  northwest   5116.50040   5140.0
2   59  female  34.800         2     no  southwest  36910.60803  24249.0
3   36    male  33.400         2    yes  southwest  38415.47400  36939.0
4   37  female  25.555         1    yes  northeast  20296.86345  21132.0

# Save the experiment

In [48]:
save_experiment('Experiment_insurance_cost 14May2020')

Experiment Succesfully Saved


# Loading saved experiment

In [49]:
saved_experiment = load_experiment('Experiment_insurance_cost 14May2020')

[22:23:53] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[22:23:53] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[22:23:53] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[22:23:53] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[22:23:53] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[22:23:53] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[22:23:53] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[22:23:53] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of re

Object
0                          Regression Setup Config
1                                   X_training Set
2                                   y_training Set
3                                       X_test Set
4                                       y_test Set
5                          Transformation Pipeline
6                       Target Inverse Transformer
7                        Compare Models Score Grid
8                                 Voting Regressor
9                      Voting Regressor Score Grid
10             Extreme Gradient Boosting Regressor
11  Extreme Gradient Boosting Regressor Score Grid
12             Extreme Gradient Boosting Regressor
13  Extreme Gradient Boosting Regressor Score Grid
14                     Gradient Boosting Regressor
15          Gradient Boosting Regressor Score Grid
16                              CatBoost Regressor
17                   CatBoost Regressor Score Grid
18                                Voting Regressor
19                     Voting Regressor Score Grid
20               Stacking Regressor (Single Layer)
21    Stacking Regressor (Single Layer) Score Grid
22                                Ridge Regression
23                     Ridge Regression Score Grid
24                                Ridge Regression
25                     Ridge Regression Score Grid
26               Stacking Regressor (Single Layer)
27    Stacking Regressor (Single Layer) Score Grid
28                                Ridge Regression
29                     Ridge Regression Score Grid
30               Stacking Regressor (Single Layer)
31    Stacking Regressor (Single Layer) Score Grid
32                                Voting Regressor
33                     Voting Regressor Score Grid
34                                 Huber Regressor
35                      Huber Regressor Score Grid
36                                Voting Regressor
37                     Voting Regressor Score Grid
38                                Voting Regressor
39                     Voting Regressor Score Grid
40                                Voting Regressor
41                     Voting Regressor Score Grid
42                                Voting Regressor
43                     Voting Regressor Score Grid
44               Stacking Regressor (Single Layer)
45    Stacking Regressor (Single Layer) Score Grid
46                           Final VotingRegressor
47                                Voting Regressor
48                     Voting Regressor Score Grid
49                           Final VotingRegressor

In [41]:
final_blend_3_loaded = saved_experiment[49]

In [50]:
new_prediction = predict_model(final_blend_3_loaded, data=data_unseen, round = 0)
new_prediction.head()

age     sex     bmi  children smoker     region      charges    Label
0   18  female  27.280         3    yes  southeast  18223.45120  19044.0
1   35    male  17.860         1     no  northwest   5116.50040   5257.0
2   59  female  34.800         2     no  southwest  36910.60803  22707.0
3   36    male  33.400         2    yes  southwest  38415.47400  37069.0
4   37  female  25.555         1    yes  northeast  20296.86345  21152.0